In [1]:
import numpy as np
import pandas as pd
import os
from utils import get_label, load_data, preprocess_dataframe, save_model, load_model, get_tuner
import xgboost as xgb
# from sklearn.preprocessing import LabelEncoder
import ydata_profiling as ydp

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
train_df, test_df = load_data()
label = get_label()

In [4]:
ydp.ProfileReport(train_df, title = 'Pandas Profiling report of "Train" set', html = {'style':{'full_width': True}})

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
input_features = train_df.columns.tolist()

In [6]:
input_features

['PassengerId',
 'Survived',
 'Pclass',
 'Name',
 'Sex',
 'Age',
 'SibSp',
 'Parch',
 'Ticket',
 'Fare',
 'Cabin',
 'Embarked']

In [7]:
input_features.remove('PassengerId')
input_features.remove('Cabin')
input_features.remove('Parch')
input_features.remove('SibSp')
input_features.remove('Name')
input_features.remove('Survived')

In [8]:
input_features

['Pclass', 'Sex', 'Age', 'Ticket', 'Fare', 'Embarked']

# Preprocess Dataset

In [9]:
X_train, y_train, X_val, y_val = preprocess_dataframe(
    train_df,
    input_features=input_features,
    drop_na=False,
    fill_na=True,
    enable_categorical=True,
)

Converting Pclass to categorical
Converting Sex to categorical
Converting Embarked to categorical


In [10]:
ydp.ProfileReport(X_train, title = 'Pandas Profiling report of "Train" set', html = {'style':{'full_width': True}})

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [11]:
ydp.ProfileReport(X_val, title = 'Pandas Profiling report of "Train" set', html = {'style':{'full_width': True}})

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [12]:
len(X_train)

712

In [13]:
X_train.head()

Pclass     Sex       Age      Fare Embarked  Has_Sibsp  Has_Parch
331      1    male  1.077308 -0.078684        S          0          0
733      2    male -0.469486 -0.377145        S          0          0
382      3    male  0.149232 -0.474867        S          0          0
704      3    male -0.263247 -0.476230        S          1          0
813      3  female -1.638174 -0.025249        S          1          1

In [14]:
# hyperparamater tuning
from sklearn.pipeline import Pipeline

hyperparameter_grid = {
    # 'classifier__eta': [0.05, 0.1, 0.3],
    # 'classifier__gamma': [0, 0.01],
    'classifier__max_depth': [6, 8, 12],
    # 'classifier__n_estimators': [100, 300],
    'classifier__learning_rate': [0.01, 0.1],
    'classifier__early_stopping_rounds': [20],
    'classifier__eval_metric': ['auc', 'error'],
    'classifier__sampling_method': ['uniform', 'gradient_based'],
    'classifier__subsample': [0.7],
    # 'classifier__colsample_bytree': [0.7, 1],
    'classifier__lambda': [0.1, 0.3]
}

pipeline = Pipeline([('classifier', xgb.XGBClassifier(
    objective='binary:logistic',
    tree_method='gpu_hist',
    enable_categorical=True,
disable_default_eval_metric=True))])




In [15]:
tuner = get_tuner(pipeline, hyperparameter_grid)
tuner.fit(X_train, y_train,
          classifier__eval_set=[(X_val, y_val)],
          )

[0]	validation_0-auc:0.85541
[1]	validation_0-auc:0.88063
[2]	validation_0-auc:0.89125
[3]	validation_0-auc:0.88507
[4]	validation_0-auc:0.88867
[5]	validation_0-auc:0.88398
[6]	validation_0-auc:0.87728
[7]	validation_0-auc:0.88012
[8]	validation_0-auc:0.87799
[9]	validation_0-auc:0.87323
[10]	validation_0-auc:0.86931
[11]	validation_0-auc:0.87079
[12]	validation_0-auc:0.87111
[13]	validation_0-auc:0.87709
[14]	validation_0-auc:0.87613
[15]	validation_0-auc:0.87432
[16]	validation_0-auc:0.87432
[17]	validation_0-auc:0.87252
[18]	validation_0-auc:0.87510
[19]	validation_0-auc:0.87561
[20]	validation_0-auc:0.87703
[21]	validation_0-auc:0.87677
[22]	validation_0-auc:0.87703
[0]	validation_0-auc:0.86532
[1]	validation_0-auc:0.88179
[2]	validation_0-auc:0.89151
[3]	validation_0-auc:0.89543
[4]	validation_0-auc:0.89543
[5]	validation_0-auc:0.89858
[6]	validation_0-auc:0.89479
[7]	validation_0-auc:0.89466
[8]	validation_0-auc:0.89363
[9]	validation_0-auc:0.89672
[10]	validation_0-auc:0.89389


[64]	validation_0-auc:0.88552
[65]	validation_0-auc:0.88514
[66]	validation_0-auc:0.88475
[67]	validation_0-auc:0.88449
[68]	validation_0-auc:0.88423
[69]	validation_0-auc:0.88449
[70]	validation_0-auc:0.88385
[71]	validation_0-auc:0.88398
[72]	validation_0-auc:0.88462
[73]	validation_0-auc:0.88462
[74]	validation_0-auc:0.88398
[75]	validation_0-auc:0.88333
[76]	validation_0-auc:0.88346
[77]	validation_0-auc:0.88295
[78]	validation_0-auc:0.88243
[79]	validation_0-auc:0.88230
[0]	validation_0-auc:0.85695
[1]	validation_0-auc:0.87143
[2]	validation_0-auc:0.87066
[3]	validation_0-auc:0.87310
[4]	validation_0-auc:0.87304
[5]	validation_0-auc:0.87349
[6]	validation_0-auc:0.86216
[7]	validation_0-auc:0.85354
[8]	validation_0-auc:0.85154
[9]	validation_0-auc:0.84723
[10]	validation_0-auc:0.84685
[11]	validation_0-auc:0.85109
[12]	validation_0-auc:0.85734
[13]	validation_0-auc:0.85991
[14]	validation_0-auc:0.85792
[15]	validation_0-auc:0.85689
[16]	validation_0-auc:0.85766
[17]	validation_0-au

[13]	validation_0-auc:0.87954
[14]	validation_0-auc:0.88147
[15]	validation_0-auc:0.88250
[16]	validation_0-auc:0.88275
[17]	validation_0-auc:0.88378
[18]	validation_0-auc:0.88443
[19]	validation_0-auc:0.88752
[20]	validation_0-auc:0.88739
[21]	validation_0-auc:0.88816
[22]	validation_0-auc:0.88816
[23]	validation_0-auc:0.88726
[24]	validation_0-auc:0.88752
[25]	validation_0-auc:0.88584
[26]	validation_0-auc:0.88481
[27]	validation_0-auc:0.88662
[28]	validation_0-auc:0.88674
[29]	validation_0-auc:0.88790
[30]	validation_0-auc:0.88662
[31]	validation_0-auc:0.88610
[32]	validation_0-auc:0.88636
[33]	validation_0-auc:0.88649
[34]	validation_0-auc:0.88636
[35]	validation_0-auc:0.88649
[36]	validation_0-auc:0.88732
[37]	validation_0-auc:0.88681
[38]	validation_0-auc:0.88758
[39]	validation_0-auc:0.88578
[40]	validation_0-auc:0.88359
[41]	validation_0-auc:0.88333
[0]	validation_0-auc:0.78327
[1]	validation_0-auc:0.79492
[2]	validation_0-auc:0.79678
[3]	validation_0-auc:0.82992
[4]	validation

[46]	validation_0-auc:0.88623
[47]	validation_0-auc:0.88571
[48]	validation_0-auc:0.88713
[49]	validation_0-auc:0.88507
[50]	validation_0-auc:0.88507
[51]	validation_0-auc:0.88584
[52]	validation_0-auc:0.88571
[53]	validation_0-auc:0.88520
[54]	validation_0-auc:0.88481
[55]	validation_0-auc:0.88481
[56]	validation_0-auc:0.88456
[57]	validation_0-auc:0.88443
[0]	validation_0-auc:0.79717
[1]	validation_0-auc:0.83662
[2]	validation_0-auc:0.82606
[3]	validation_0-auc:0.84646
[4]	validation_0-auc:0.84891
[5]	validation_0-auc:0.84923
[6]	validation_0-auc:0.84723
[7]	validation_0-auc:0.85663
[8]	validation_0-auc:0.85882
[9]	validation_0-auc:0.86486
[10]	validation_0-auc:0.86332
[11]	validation_0-auc:0.86815
[12]	validation_0-auc:0.86403
[13]	validation_0-auc:0.86409
[14]	validation_0-auc:0.86178
[15]	validation_0-auc:0.86139
[16]	validation_0-auc:0.85985
[17]	validation_0-auc:0.86306
[18]	validation_0-auc:0.86409
[19]	validation_0-auc:0.86338
[20]	validation_0-auc:0.86493
[21]	validation_0-au

[29]	validation_0-auc:0.85142
[30]	validation_0-auc:0.85245
[31]	validation_0-auc:0.85219
[32]	validation_0-auc:0.85180
[33]	validation_0-auc:0.85039
[34]	validation_0-auc:0.85103
[35]	validation_0-auc:0.85283
[36]	validation_0-auc:0.85283
[37]	validation_0-auc:0.85296
[38]	validation_0-auc:0.85470
[39]	validation_0-auc:0.85483
[40]	validation_0-auc:0.85573
[41]	validation_0-auc:0.85766
[42]	validation_0-auc:0.85753
[43]	validation_0-auc:0.85714
[44]	validation_0-auc:0.85766
[45]	validation_0-auc:0.85933
[46]	validation_0-auc:0.85946
[47]	validation_0-auc:0.85985
[48]	validation_0-auc:0.85985
[49]	validation_0-auc:0.85997
[50]	validation_0-auc:0.85997
[51]	validation_0-auc:0.85972
[52]	validation_0-auc:0.85972
[53]	validation_0-auc:0.86036
[54]	validation_0-auc:0.85907
[55]	validation_0-auc:0.85946
[56]	validation_0-auc:0.85972
[57]	validation_0-auc:0.85920
[58]	validation_0-auc:0.85830
[59]	validation_0-auc:0.85740
[60]	validation_0-auc:0.85856
[61]	validation_0-auc:0.85830
[62]	valid

...

[2]	validation_0-error:0.17318
[3]	validation_0-error:0.18436
[4]	validation_0-error:0.17877
[5]	validation_0-error:0.17318
[6]	validation_0-error:0.16760
[7]	validation_0-error:0.17318
[8]	validation_0-error:0.18436
[9]	validation_0-error:0.20112
[10]	validation_0-error:0.17877
[11]	validation_0-error:0.17877
[12]	validation_0-error:0.17877
[13]	validation_0-error:0.17877
[14]	validation_0-error:0.17318
[15]	validation_0-error:0.17318
[16]	validation_0-error:0.18994
[17]	validation_0-error:0.18436
[18]	validation_0-error:0.18436
[19]	validation_0-error:0.16201
[20]	validation_0-error:0.16201
[21]	validation_0-error:0.16760
[22]	validation_0-error:0.16201
[23]	validation_0-error:0.16760
[24]	validation_0-error:0.16201
[25]	validation_0-error:0.17877
[26]	validation_0-error:0.17877
[27]	validation_0-error:0.16760
[28]	validation_0-error:0.17877
[29]	validation_0-error:0.17877
[30]	validation_0-error:0.17877
[31]	validation_0-error:0.17877
[32]	validation_0-error:0.17877
[33]	validation_

[36]	validation_0-error:0.16760
[37]	validation_0-error:0.16760
[38]	validation_0-error:0.17877
[39]	validation_0-error:0.16760
[40]	validation_0-error:0.17877
[41]	validation_0-error:0.17318
[42]	validation_0-error:0.17318
[43]	validation_0-error:0.17877
[44]	validation_0-error:0.17877
[45]	validation_0-error:0.17877
[46]	validation_0-error:0.17318
[47]	validation_0-error:0.17877
[48]	validation_0-error:0.17318
[49]	validation_0-error:0.17318
[50]	validation_0-error:0.17318
[51]	validation_0-error:0.17318
[52]	validation_0-error:0.17318
[53]	validation_0-error:0.17318
[54]	validation_0-error:0.17318
[55]	validation_0-error:0.16760
[0]	validation_0-error:0.20112
[1]	validation_0-error:0.20112
[2]	validation_0-error:0.17877
[3]	validation_0-error:0.18994
[4]	validation_0-error:0.18994
[5]	validation_0-error:0.19553
[6]	validation_0-error:0.20112
[7]	validation_0-error:0.19553
[8]	validation_0-error:0.19553
[9]	validation_0-error:0.18994
[10]	validation_0-error:0.18994
[11]	validation_0-

[24]	validation_0-error:0.18994
[25]	validation_0-error:0.18994
[26]	validation_0-error:0.18994
[27]	validation_0-error:0.18436
[0]	validation_0-error:0.24022
[1]	validation_0-error:0.20670
[2]	validation_0-error:0.20670
[3]	validation_0-error:0.19553
[4]	validation_0-error:0.19553
[5]	validation_0-error:0.19553
[6]	validation_0-error:0.19553
[7]	validation_0-error:0.19553
[8]	validation_0-error:0.19553
[9]	validation_0-error:0.19553
[10]	validation_0-error:0.19553
[11]	validation_0-error:0.18994
[12]	validation_0-error:0.18994
[13]	validation_0-error:0.18994
[14]	validation_0-error:0.18994
[15]	validation_0-error:0.18436
[16]	validation_0-error:0.18436
[17]	validation_0-error:0.18436
[18]	validation_0-error:0.18436
[19]	validation_0-error:0.18994
[20]	validation_0-error:0.18994
[21]	validation_0-error:0.17877
[22]	validation_0-error:0.18436
[23]	validation_0-error:0.18436
[24]	validation_0-error:0.18436
[25]	validation_0-error:0.18436
[26]	validation_0-error:0.18436
[27]	validation_0-

[0]	validation_0-auc:0.81300
[1]	validation_0-auc:0.84093
[2]	validation_0-auc:0.84344
[3]	validation_0-auc:0.86705
[4]	validation_0-auc:0.87098
[5]	validation_0-auc:0.87098
[6]	validation_0-auc:0.87079
[7]	validation_0-auc:0.86744
[8]	validation_0-auc:0.87053
[9]	validation_0-auc:0.87143
[10]	validation_0-auc:0.87362
[11]	validation_0-auc:0.87638
[12]	validation_0-auc:0.87587
[13]	validation_0-auc:0.87651
[14]	validation_0-auc:0.87265
[15]	validation_0-auc:0.87317
[16]	validation_0-auc:0.87658
[17]	validation_0-auc:0.87934
[18]	validation_0-auc:0.87896
[19]	validation_0-auc:0.87979
[20]	validation_0-auc:0.87812
[21]	validation_0-auc:0.87928
[22]	validation_0-auc:0.88314
[23]	validation_0-auc:0.88662
[24]	validation_0-auc:0.88481
[25]	validation_0-auc:0.88739
[26]	validation_0-auc:0.88456
[27]	validation_0-auc:0.88366
[28]	validation_0-auc:0.88571
[29]	validation_0-auc:0.88378
[30]	validation_0-auc:0.88353
[31]	validation_0-auc:0.88507
[32]	validation_0-auc:0.88366
[33]	validation_0-au

GridSearchCV(cv=5,
             estimator=Pipeline(steps=[('classifier',
                                        XGBClassifier(base_score=None,
                                                      booster=None,
                                                      callbacks=None,
                                                      colsample_bylevel=None,
                                                      colsample_bynode=None,
                                                      colsample_bytree=None,
                                                      disable_default_eval_metric=True,
                                                      early_stopping_rounds=None,
                                                      enable_categorical=True,
                                                      eval_metric=None,
                                                      feature_types=None,
                                                      gamma=None, gpu_id=None,
                                                      grow_policy=None,
                                                      importa...
                                                      num_parallel_tree=None,
                                                      predictor=None, ...))]),
             param_grid={'classifier__early_stopping_rounds': [20],
                         'classifier__eval_metric': ['auc', 'error'],
                         'classifier__lambda': [0.1, 0.3],
                         'classifier__learning_rate': [0.01, 0.1],
                         'classifier__max_depth': [6, 8, 12],
                         'classifier__sampling_method': ['uniform',
                                                         'gradient_based'],
                         'classifier__subsample': [0.7]},
             return_train_score=True)

In [16]:
best_model = tuner.best_estimator_

In [17]:
def print_scores(model, train_val_set: list[tuple]):
    train_score = model.score(train_val_set[0][0], train_val_set[0][1])
    val_score = model.score(train_val_set[1][0], train_val_set[1][1])
    print(f'Train Score: {train_score}\nVal score: {val_score}')

In [18]:
print_scores(best_model, [(X_train, y_train), (X_val, y_val)])

Train Score: 0.9087078651685393
Val score: 0.8379888268156425


In [19]:
# save_model(best_model, 'xgb_best_model')

In [20]:
m = load_model('xgb_best_model')
print_scores(m, [(X_train, y_train), (X_val, y_val)])

Train Score: 0.9087078651685393
Val score: 0.8379888268156425


In [21]:
best_model.get_params()['classifier']

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, disable_default_eval_metric=True,
              early_stopping_rounds=20, enable_categorical=True,
              eval_metric='auc', feature_types=None, gamma=None, gpu_id=None,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, lambda=0.3, learning_rate=0.1,
              max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=8, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              n_estimators=100, n_jobs=None, num_parallel_tree=None, ...)

In [22]:
test_df.head()

PassengerId  Pclass                                          Name     Sex  \
0          892       3                              Kelly, Mr. James    male   
1          893       3              Wilkes, Mrs. James (Ellen Needs)  female   
2          894       2                     Myles, Mr. Thomas Francis    male   
3          895       3                              Wirz, Mr. Albert    male   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)  female   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  
0  34.5      0      0   330911   7.8292   NaN        Q  
1  47.0      1      0   363272   7.0000   NaN        S  
2  62.0      0      0   240276   9.6875   NaN        Q  
3  27.0      0      0   315154   8.6625   NaN        S  
4  22.0      1      1  3101298  12.2875   NaN        S

In [23]:
test_df = preprocess_dataframe(
    test_df,
    input_features=input_features,
    drop_na=False,
    fill_na=True,
    enable_categorical=True,
    test_split=None
)

Converting Pclass to categorical
Converting Sex to categorical
Converting Embarked to categorical


In [24]:
test_df.head()

Pclass     Sex       Age      Fare Embarked  Has_Sibsp  Has_Parch
0      3    male  0.259288 -0.498550        Q          0          0
1      3  female  1.122800 -0.513417        S          1          0
2      2    male  2.159014 -0.465231        Q          0          0
3      3    male -0.258819 -0.483609        S          0          0
4      3  female -0.604223 -0.418614        S          1          1

In [25]:
m.predict(test_df)

array([0, 0, 0, 0, 0, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1,
       1, 1, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 1,
       1, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1,
       1, 0, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 0, 0, 0, 1, 1,
       1, 1, 0, 0, 1, 0, 0, 0, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0,
       0, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0,
       0, 0, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 1,
       0, 0, 1, 1, 0, 1, 1, 1, 1, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1,
       1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 0, 1, 1,
       0, 1, 0, 1, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 0, 1, 0,
       1, 0, 1, 0, 1, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1,
       0, 0, 0, 0, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1,
       0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 1, 1, 0, 1, 0,
       0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0,